In [ ]:
#get the structures from uniprot for the swissport matches

#import the bfvd ones from curnagl

#get uniprot metadata

#run chainsaw

#cut structurure into chunks using biopython

#cluster the chunks using homology graph + louvain

#separte the clusters of chunks into folders



#run ft1 and ft2 on the folders containining jelly roll.

#label phylo. fitch... euk/vir transfers. chunk architecture changes, viral clades, T number in capsid orga

#

In [28]:
cd /home/dmoi/projects/foldtree2/families/jelly_roll

/home/dmoi/projects/foldtree2/families/jelly_roll


In [29]:
import requests
import os

def download_pdb(pdb_id, out_dir='.' , overwrite=False):
	"""
	Download a PDB file from RCSB PDB given its identifier.

	Args:
		pdb_id (str): The PDB identifier (e.g., '1abc').
		out_dir (str): Output directory to save the file.

	Returns:
		str: Path to the downloaded PDB file.
	"""
	if os.path.exists(f'{out_dir}/{pdb_id}.pdb') and not overwrite:
		return f'{out_dir}/{pdb_id}.pdb'
	pdb_id = pdb_id.lower()
	url = f'https://files.rcsb.org/download/{pdb_id}.pdb'
	out_path = f'{out_dir}/{pdb_id}.pdb'
	response = requests.get(url)
	if response.status_code == 200:
		with open(out_path, 'w') as f:
			f.write(response.text)
		return out_path
	else:
		raise ValueError(f"Failed to download PDB file for {pdb_id}: HTTP {response.status_code}")
	



In [30]:
#capsid architectures from https://doi.org/10.3390/v13112191

capsid_architectures = pd.read_csv( './t_number.csv')
print(capsid_architectures.head())

           Family           Genus  T#    GP   pdb
0    Adenoviridae  Mastadenovirus   1    19  4aqq
1  Mastadenovirus            pT25  21  6b1t   NaN
2        Bacteria      Haliangium   9     6  6mzx
3    Birnaviridae  Aquabirnavirus   1     7  3ide
4   Avibirnavirus             NaN   1    12  2df7


In [31]:
seed_dir = './seed_structs'
import tqdm
pdbset = set(capsid_architectures['pdb'].dropna().str.lower().unique())
for pdb_id in tqdm.tqdm(pdbset):
	try:
		pdb_path = download_pdb(pdb_id, out_dir=seed_dir)
	except ValueError as e:
		print(e)
	

  2%|█▉                                                                                    | 3/132 [00:03<02:30,  1.17s/it]

Failed to download PDB file for 6mzx: HTTP 404


 17%|██████████████▏                                                                      | 22/132 [00:06<00:30,  3.57it/s]

Failed to download PDB file for 6nhj: HTTP 404


 21%|██████████████████                                                                   | 28/132 [00:07<00:22,  4.61it/s]

...

Failed to download PDB file for 6e9d: HTTP 404


 78%|█████████████████████████████████████████████████████████████████▌                  | 103/132 [00:31<00:14,  2.00it/s]

Failed to download PDB file for 5us7: HTTP 404


100%|████████████████████████████████████████████████████████████████████████████████████| 132/132 [00:35<00:00,  3.77it/s]

Failed to download PDB file for 6bwx: HTTP 404


In [32]:
import time

def map_pdb_to_uniprot(capsid_architectures):
	"""
	Map PDB identifiers to UniProt codes using the 'pdb' column in capsid_architectures DataFrame.
	Returns a dictionary {pdb_id: uniprot_code or None}.
	"""
	# Remove rows with missing pdb ids
	pdb_df = capsid_architectures.dropna(subset=['pdb'])
	# Use UniProt mapping API
	url = "https://rest.uniprot.org/idmapping/run"
	pdb_ids = pdb_df['pdb'].str.lower().unique().tolist()
	# Prepare request
	params = {
		"from": "PDB_ID",
		"to": "UniProtKB",
		"ids": ",".join(pdb_ids)
	}
	# Submit mapping job
	r = requests.post(url, data=params)
	print(r)
	job_id = r.json()['jobId']
	# Poll for results
	result_url = f"https://rest.uniprot.org/idmapping/results/{job_id}"
	while True:
		resp = requests.get(result_url)
		if resp.status_code == 200 and 'results' in resp.json():
			break
		time.sleep(1)
	# Parse results
	mapping = {}
	for entry in resp.json()['results']:
		pdb = entry['from'].lower()
		uniprot = entry['to']
		mapping[pdb] = uniprot
	# Fill in None for unmapped
	for pdb in pdb_ids:
		if pdb not in mapping:
			mapping[pdb] = None
	return mapping

# Example usage:
# pdb_to_uniprot = map_pdb_to_uniprot(capsid_architectures)
pdd2uniprot = map_pdb_to_uniprot(capsid_architectures)
capsid_architectures['uniprot'] = capsid_architectures['pdb'].str.lower().map(pdd2uniprot)
print(capsid_architectures.head())

<Response [400]>


KeyError: 'jobId'

In [35]:
#read foldseek results
import pandas as pd
swissprot_df = pd.read_table('./jellyroll_vs_swissprot.m8', header=None, names='query,target,fident,alnlen,mismatch,gapopen,qstart,qend,tstart,tend,evalue,bits,prob,alntmscore,lddt'.split(',') )
print(swissprot_df.head()	)
len(swissprot_df)

    query                     target  fident  alnlen  mismatch  gapopen  \
0  2y26_M      AF-A2AJA7-F1-model_v4   0.070     536       292       41   
1  2y26_M      AF-Q6BH66-F1-model_v4   0.059     538       315       36   
2  2y26_M      AF-Q9HFC8-F1-model_v4   0.097     542       292       40   
3  2y26_M  AF-A0A1P8AWH8-F1-model_v4   0.091     569       328       42   
4  2y26_M      AF-C6CRV0-F1-model_v4   0.091     548       333       46   

   qstart  qend  tstart  tend    evalue  bits   prob  alntmscore    lddt  
0      48   499     728  1141  0.000007    74  0.961      0.1785  0.2702  
1       2   494     372   763  0.000053    72  0.949      0.1938  0.3060  
2       2   504     411   794  0.000024    71  0.941      0.1995  0.2611  
3       7   499     100   555  0.000002    71  0.941      0.1598  0.2504  
4       7   500      73   509  0.000033    65  0.872      0.1730  0.2586  


350858

In [36]:
swissprot_df['target_uni_Id'] = swissprot_df['target'].map( lambda x : x.split('-')[1] ) 
print(swissprot_df.head())

    query                     target  fident  alnlen  mismatch  gapopen  \
0  2y26_M      AF-A2AJA7-F1-model_v4   0.070     536       292       41   
1  2y26_M      AF-Q6BH66-F1-model_v4   0.059     538       315       36   
2  2y26_M      AF-Q9HFC8-F1-model_v4   0.097     542       292       40   
3  2y26_M  AF-A0A1P8AWH8-F1-model_v4   0.091     569       328       42   
4  2y26_M      AF-C6CRV0-F1-model_v4   0.091     548       333       46   

   qstart  qend  tstart  tend    evalue  bits   prob  alntmscore    lddt  \
0      48   499     728  1141  0.000007    74  0.961      0.1785  0.2702   
1       2   494     372   763  0.000053    72  0.949      0.1938  0.3060   
2       2   504     411   794  0.000024    71  0.941      0.1995  0.2611   
3       7   499     100   555  0.000002    71  0.941      0.1598  0.2504   
4       7   500      73   509  0.000033    65  0.872      0.1730  0.2586   

  target_uni_Id  
0        A2AJA7  
1        Q6BH66  
2        Q9HFC8  
3    A0A1P8AWH8  
4 

In [37]:
bfvd_df = pd.read_table('./jellyroll_vs_bfvd.m8', header=None, names='query,target,fident,alnlen,mismatch,gapopen,qstart,qend,tstart,tend,evalue,bits,prob,alntmscore,lddt'.split(','))
print(bfvd_df.head())
len(bfvd_df)

    query                                             target  fident  alnlen  \
0  4rft_9  Q88166_unrelaxed_rank_001_alphafold2_ptm_model...   0.918     159   
1  4rft_9  A0A411D379_unrelaxed_rank_001_alphafold2_ptm_m...   0.345     165   
2  4rft_9  D1MGN1_unrelaxed_rank_001_alphafold2_ptm_model...   0.347     164   
3  4rft_9  A0A1L3KHR7_unrelaxed_rank_001_alphafold2_ptm_m...   0.309     165   
4  4rft_9  A0A8A5TMF5_unrelaxed_rank_001_alphafold2_ptm_m...   0.325     160   

   mismatch  gapopen  qstart  qend  tstart  tend        evalue  bits  prob  \
0        13        0       4   162       2   160  3.180000e-30  1148   1.0   
1       103        2       3   163      69   232  2.747000e-19   693   1.0   
2       102        2       4   163      52   214  2.585000e-19   683   1.0   
3       109        4       2   163      60   222  2.297000e-18   652   1.0   
4       107        1       2   160      67   226  8.216000e-18   646   1.0   

   alntmscore    lddt  
0      0.9798  0.9162  
1 

562070

In [38]:
bfvd_df['target_uni_Id'] = bfvd_df['target'].map( lambda x : x.split('_')[0] )
print(bfvd_df.head())

    query                                             target  fident  alnlen  \
0  4rft_9  Q88166_unrelaxed_rank_001_alphafold2_ptm_model...   0.918     159   
1  4rft_9  A0A411D379_unrelaxed_rank_001_alphafold2_ptm_m...   0.345     165   
2  4rft_9  D1MGN1_unrelaxed_rank_001_alphafold2_ptm_model...   0.347     164   
3  4rft_9  A0A1L3KHR7_unrelaxed_rank_001_alphafold2_ptm_m...   0.309     165   
4  4rft_9  A0A8A5TMF5_unrelaxed_rank_001_alphafold2_ptm_m...   0.325     160   

   mismatch  gapopen  qstart  qend  tstart  tend        evalue  bits  prob  \
0        13        0       4   162       2   160  3.180000e-30  1148   1.0   
1       103        2       3   163      69   232  2.747000e-19   693   1.0   
2       102        2       4   163      52   214  2.585000e-19   683   1.0   
3       109        4       2   163      60   222  2.297000e-18   652   1.0   
4       107        1       2   160      67   226  8.216000e-18   646   1.0   

   alntmscore    lddt target_uni_Id  
0      0.979

In [39]:
#filter both dfs on proba > 90
bfvd_df = bfvd_df[bfvd_df['prob'] > .90]
swissprot_df = swissprot_df[swissprot_df['prob'] > .90]

In [45]:
entries = set( bfvd_df['target_uni_Id'].dropna().unique() ) | set( swissprot_df['target_uni_Id'].dropna().unique() )
print( len(entries) )

#remove all entries that start with UPI
entries = { e for e in entries if not e.startswith('UPI') }

12166


In [ ]:
import foldtree2.src.AFDB_tools as afdb_tools
metadata = afdb_tools.grab_entries( list(entries) )

          Entry Name       Entry  \
1          CD4_MOUSE      P06332   
2         HA14_MOUSE      P14427   
3        UNC5D_HUMAN      Q6UXZ4   
4        ZPBP2_MOUSE      Q6X786   
5         MUSK_CHICK      Q8AXY6   
7        K0FHP1_IBDV      K0FHP1   
8         ZIG6_CAEEL      Q22125   
9        MO2R2_HUMAN      Q6Q8B3   
10       HV103_HUMAN  A0A0C4DH29   
11       TVB74_HUMAN  A0A1B0GX95   
12        KDUI_ECO55      B7LF20   
13        UNIV_STRPU      P48970   
14       CR1AE_BACTL      Q03748   
15       AMGO2_PONAB      Q5R7M3   
16  A0A142D861_9VIRU  A0A142D861   
17  A0A2S0S4Q6_9VIRU  A0A2S0S4Q6   
18  A0A346BLH1_9REOV  A0A346BLH1   
19  A0A514DBE9_9VIRU  A0A514DBE9   
20    A0A650GCM8_HEV  A0A650GCM8   
21  A0A823A1V0_9VIRU  A0A823A1V0   
22        CMOA_ECO5E      B5YR15   
23      D1MN99_9DELA      D1MN99   
24       KV5A6_MOUSE      P01638   
25        RLMC_YERPN      Q1CGA8   
26  A0A126G9J3_9VIRU  A0A126G9J3   
27  A0A1D6ZNJ1_9SECO  A0A1D6ZNJ1   
28  A0A1L3KIJ2_9VIRU  A0A1L3

In [47]:
#save the metadata
metadata.to_csv('./jelly_roll_metadata.csv', index=False)
print(metadata.head())

    Entry Name   Entry                              Gene Names  \
0    CD4_MOUSE  P06332                                     Cd4   
1   HA14_MOUSE  P14427                                   H2-D1   
2  UNC5D_HUMAN  Q6UXZ4  UNC5D KIAA1777 UNC5H4 UNQ6012/PRO34692   
3  ZPBP2_MOUSE  Q6X786                                   Zpbp2   
4   MUSK_CHICK  Q8AXY6                                    MUSK   

                                       Protein names  Reviewed  \
0  T-cell surface glycoprotein CD4 (T-cell differ...  reviewed   
1  H-2 class I histocompatibility antigen, D-P al...  reviewed   
2  Netrin receptor UNC5D (Protein unc-5 homolog 4...  reviewed   
3                   Zona pellucida-binding protein 2  reviewed   
4  Muscle, skeletal receptor tyrosine protein kin...  reviewed   

                                     Protein names.1                 Organism  \
0  T-cell surface glycoprotein CD4 (T-cell differ...     Mus musculus (Mouse)   
1  H-2 class I histocompatibility antigen, D

In [ ]:
#grab the structures from AFDB for the swissprot matches
import foldtree2.src.AFDB_tools as afdb_tools

get_structs = False
if get_structs == True:
	for entry in tqdm.tqdm(metadata.Entry.unique()):
		afdb_tools.grab_struct(entry, structfolder='./structs', overwrite=False)

In [53]:
#Tranfer all the bfvd structures to the same folder
import shutil
import os

bfvd_structs = set(bfvd_df['target_uni_Id'].dropna().unique())
for entry in tqdm.tqdm(metadata.Entry.unique()):
	if entry in bfvd_structs:
		src_path = f'/home/dmoi/UNILMNT/datasets/bfvd/{entry}.pdb'
		dest_path = f'./structs/{entry}.pdb'
		if os.path.exists(src_path):
			shutil.copy(src_path, dest_path)
		else:
			print(f"Warning: {src_path} does not exist, skipping.")

 86%|████████████████████████████████████████████████████████████████████▊           | 10351/12030 [04:23<00:28, 59.85it/s]

 86%|█████████████████████████████████████████████████████████████████████           | 10392/12030 [04:24<00:27, 58.95it/s]

 87%|█████████████████████████████████████████████████████████████████████▏          | 10412/12030 [04:24<00:46, 34.43it/s]

 87%|█████████████████████████████████████████████████████████████████████▍          | 10437/12030 [04:25<00:36, 43.99it/s]

 88%|██████████████████████████████████████████████████████████████████████          | 10543/12030 [04:27<00:27, 53.40it/s]

...

 99%|███████████████████████████████████████████████████████████████████████████████▍| 11950/12030 [05:03<00:01, 40.78it/s]

100%|███████████████████████████████████████████████████████████████████████████████▋| 11990/12030 [05:03<00:00, 75.99it/s]

100%|███████████████████████████████████████████████████████████████████████████████▊| 12007/12030 [05:04<00:00, 45.82it/s]

100%|███████████████████████████████████████████████████████████████████████████████▉| 12024/12030 [05:04<00:00, 41.39it/s]

100%|████████████████████████████████████████████████████████████████████████████████| 12030/12030 [05:05<00:00, 39.43it/s]


In [61]:
import requests

def get_virusworld_data_for_taxa(tax_ids):
	"""
	Retrieve virus information from VirusWorld for a list of taxonomy IDs.

	Args:
		tax_ids (iterable): List or set of NCBI taxonomy IDs (as int or str).

	Returns:
		dict: Mapping from taxonomy_id to response JSON (or None if not found/error).
	"""
	base_url = "https://virus-world.org/api.php/entry/"
	results = {}
	for tax_id in tax_ids:
		url = f"{base_url}{tax_id}"
		try:
			resp = requests.get(url, headers={'accept': 'application/json'}, timeout=10)
			if resp.status_code == 200:
				results[tax_id] = resp.json()
			else:
				results[tax_id] = None
		except Exception as e:
			print(f"Error retrieving taxonomy {tax_id}: {e}")
			results[tax_id] = None
	return results

# https://virus-world.org/
# Example usage:
virus_data = get_virusworld_data_for_taxa([10246, 539351])
print(virus_data)
#transform the data into a dataframe
import pandas as pd
def transform_virus_data(virus_data):
	"""
	Transform the virus data dictionary into a DataFrame.
	
	Args:
		virus_data (dict): Dictionary mapping taxonomy IDs to virus data.
		
	Returns:
		DataFrame: Pandas DataFrame with columns for taxonomy ID, name, and other attributes.
	"""
	data = []
	for tax_id, info in virus_data.items():
		if info is not None:
			data.append({
				'tax_id': tax_id,
				'name': info.get('name', ''),
				'genus': info.get('genus', ''),
				'family': info.get('family', ''),
				'order': info.get('order', ''),
				'host': info.get('host', ''),
				'baltimore_genome': info.get('baltimore_genome', ''),
				'description': info.get('description', '')
			})
	return pd.DataFrame(data)

virus_data = transform_virus_data(virus_data)
print(virus_data)

{10246: {'tax_id': 10246, 'name_txt': 'Vaccinia virus LC16MO', 'name_class': 'scientific name', 'common_name': None, 'equivalent_name': 'Vaccinia virus (strain LC16MO)', 'acronym': None, 'rank': 'no rank', 'parent_tax_id': 10245, 'host': 'human,vertebrates', 'species': 'Orthopoxvirus vaccinia', 'genus': 'Orthopoxvirus', 'family': 'Poxviridae', 'order': 'Chitovirales', 'class': 'Pokkesviricetes', 'phylum': 'Nucleocytoviricota', 'kingdom': 'Bamfordvirae', 'genome': 'Varidnaviria', 'baltimore_genome': 'dsDNA', 'superkingdom': 'Viruses', 'has_structure': 0, 'disease_info_parent': 10245, 'fullnamelineage': 'Viruses; Varidnaviria; Bamfordvirae; Nucleocytoviricota; Pokkesviricetes; Chitovirales; Poxviridae; Chordopoxvirinae; Orthopoxvirus; Orthopoxvirus vaccinia; ', 'structures': {'results': [], 'total': 0}, 'uniprot_ids': {'results': [{'tax_id': 10246, 'uniprotkb_id': 'Q49PZ0', 'entry_name': 'PG021_VACC0', 'protein_names': 'Host range factor p28', 'gene_name': 'OPG021', 'organism': 'VACV', '

In [ ]:
#map viral tax data to the uniprot metadata

In [ ]:
#run chainsaw on the structs

#read the chainsaw results